In [43]:
# pip install sentence-transformers numpy
from sentence_transformers import SentenceTransformer
import numpy as np

In [44]:
transformers = [
    "sentence-transformers/all-mpnet-base-v2", # BERT-based model
    "intfloat/e5-small-v2",
    "sentence-transformers/all-MiniLM-L6-v2" # smaller model
    ]

# load a small open embedding model
model = SentenceTransformer(transformers[2])



In [45]:
# define your words
words = ["king", "queen", "man", "woman", "male", "female", "prince", "princess",
         "city", "village", "cat", "dog", "doctor", "nurse", "medical", "hospital", "job", "human", "girl", "boy", 
         "kindness", "strength", "attributes", "kingly attributes", "royal attributes", "queenly attributes", "dexter", "murderer", "serial killer", 
         "helper", "friend", "companion", "who can help me with a murder?", "jakob", "dan", "frank",
         "boner", "period", "baby", "child"]

f = open("en_US-large.txt")

words = f.read().splitlines()

# encode & normalize
embeds = model.encode(words, normalize_embeddings=True)
word2vec = dict(zip(words, embeds))

import numpy as np

def arithmetic(expr, word2vec, normalize=True):
    """
    Parse a simple expression like "king - man + woman" and return:
      {
        "terms": [{"word": "king", "sign": +1, "vector": ...}, ...],
        "unknown": ["..."],
        "result_vector": np.ndarray
      }
    Rules:
      - Tokens separated by spaces.
      - Supported operators: + and -
      - Leading + or - is allowed; default sign is +.
    """
    # figure out embedding dim robustly
    try:
        dim = next(iter(word2vec.values())).shape[-1]
    except StopIteration:
        raise ValueError("word2vec is empty")

    tokens = expr.split()
    sign = +1
    result = np.zeros(dim, dtype=float)
    terms = []
    unknown = []

    for tok in tokens:
        if tok == '+':
            sign = +1
        elif tok == '-':
            sign = -1
        else:
            if tok in word2vec:
                vec = word2vec[tok].astype(float)
                signed_vec = sign * vec
                result += signed_vec
                terms.append({"word": tok, "sign": int(sign), "vector": vec})
                # after applying, reset sign to + for implicit '+ word'
                sign = +1
            else:
                unknown.append(tok)
                # reset sign so "- unknown + x" doesn't carry the '-'
                sign = +1

    if normalize:
        norm = np.linalg.norm(result)
        if norm > 0:
            result = result / norm

    return {"terms": terms, "unknown": unknown, "result_vector": result}

    



In [ ]:
# female - male direction in the ORIGINAL embedding space (dim = D)
f_set = ["woman","female", "mom", "mother", "aunt", "niece","girl","queen","she","her","mother", "princess", "feminine", "madam", "lady", "miss",
         "daughter", "sister", "wife", "motherhood", "girlfriend", "grandmother", "granddaughter",
         "vagina", "pussy", "breasts", "boobs", "period", "menstruation"]
m_set = ["man","male","boy", "dad", "father", "uncle", "nephew","king","he","him","father, prince, masculine, sir, gentleman, mister", 
         "son", "brother", "husband", "fatherhood", "boyfriend", "grandfather", "grandson",
         "cock", "penis", "balls", "testicles", "erection", "boner"]

f_vec = np.sum([word2vec[w] for w in f_set if w in word2vec], axis=0)
m_vec = np.sum([word2vec[w] for w in m_set if w in word2vec], axis=0)
gender_dir = m_vec - f_vec
gender_dir /= np.linalg.norm(gender_dir)



vector_target = gender_dir
# vector_target = 

# result = arithmetic("woman + female + girl - man - male - boy", word2vec)
# result_vector = result["result_vector"]

word = "stay at home"

vector_target /= np.linalg.norm(vector_target)

cos = np.dot(model.encode(word), vector_target)
print(f"{word}\tf < {cos:.2f} < m")
# result_vector /= np.linalg.norm(result_vector)

# compute cosine similarity
def cosine(a, b): return np.dot(a, b)
scores = {w: cosine(vector_target, v) for w, v in word2vec.items()}
sorted_scores = sorted(scores.items(), key=lambda item: -item[1])
# for w, s in sorted_scores:
#     print(f"{w:10s} {s:.2f}")

new_male_sort = [w for w, s in sorted_scores if s > 0.25]
new_female_sort = [w for w, s in sorted_scores if s < -0.25]

new_gender_vector =  np.mean([word2vec[w] for w in new_male_sort], axis=0) - np.mean([word2vec[w] for w in new_female_sort], axis=0)
new_gender_vector /= np.linalg.norm(new_gender_vector)
vector_target = new_gender_vector


cos = np.dot(model.encode(word), vector_target)
print(f"{word}\tf < {cos:.2f} < m")

print("New male words:", new_male_sort)
print("New female words:", new_female_sort)

# compute new cosine similarity
scores = {w: cosine(vector_target, v) for w, v in word2vec.items()}
sorted_scores = sorted(scores.items(), key=lambda item: -item[1])
# for w, s in sorted_scores:
#     print(f"{w:10s} {s:.2f}")

stay at home	f < -0.10 < m
stay at home	f < nan < m
New male words: []
New female words: ['Mirzam', 'purse', 'Hinayana', 'floras', 'bridals', 'Harriett', "Belinda's", 'transgenders', 'personable', 'chiselled', 'couthie', "Vivian's", 'kiddos', 'Virgie', 'alexia', 'ugly', 'anneals', 'Edessa', "Magdalene's", 'columella', 'jollies', 'Laclos', "Cora's", 'database', 'Florentia', 'loyalties', 'Kathiawar', 'Tripura', 'Tracey', "Amy's", 'estrange', 'perorates', "Rosanna's", 'childless', 'Ivy', 'ivy', 'coupes', 'eunuchize', 'niceties', 'rosiest', "Frenchwomen's", 'Cressida', 'Chrystal', "chrysalis's", 'Portia', 'tesselate', 'braes', 'Ebony', 'ebony', "Zoe's", "Stacy's", 'charades', 'Patty', 'patty', 'Rachael', 'administrable', 'malvasia', 'Leukas', 'Celaeno', 'Agana', 'administrated', 'Liao', 'Lala', 'magnoliaceous', "Clair's", "sissy's", 'Sherry', 'sherry', 'harems', 'Balenciaga', 'Mahayana', 'chickadees', 'Ronda', 'missals', 'impermanence', 'Mai', 'Cannes', 'thighs', "Mallory's", 'fusibility',

In [47]:
import numpy as np
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt

# Step 1. Build your feature matrix (rows = words, cols = embedding dimensions)
words = list(word2vec.keys())
X = np.stack([word2vec[w] for w in words])  # shape (num_words, embed_dim)

# Step 2. Create and fit PCA
pca = PCA(n_components=3084)
X_pca = pca.fit_transform(X)

# female - male direction in the ORIGINAL embedding space (dim = D)
f_set = ["woman","female","girl","queen","she","her","mother","actress"]
m_set = ["man","male","boy","king","he","him","father","actor"]

f_vec = np.mean([word2vec[w] for w in f_set if w in word2vec], axis=0)
m_vec = np.mean([word2vec[w] for w in m_set if w in word2vec], axis=0)
gender_dir = f_vec - m_vec

examined_vector = gender_dir

sims = (pca.components_ / np.linalg.norm(pca.components_, axis=1, keepdims=True)) @ examined_vector
idx = np.argmax(np.abs(sims))
print(f"PC{idx+1} alignment with gender axis: {sims[idx]:.3f}")

# Principal axes in ORIGINAL space: (n_components, D)
axes = pca.components_

# Cosine similarity with each axis
def cosine(a, b):
    return np.dot(a, b) / (np.linalg.norm(a) * np.linalg.norm(b))

fv = examined_vector / np.linalg.norm(examined_vector)
axes_norm = axes / np.linalg.norm(axes, axis=1, keepdims=True)
sims = axes_norm @ fv  # shape: (n_components,)

idx = np.argmax(np.abs(sims))  # use abs if you don't care about sign
print(f"Most aligned PC: PC-{idx+1} with cosine {sims[idx]:.3f}")



ValueError: n_components=3084 must be between 0 and min(n_samples, n_features)=384 with svd_solver='covariance_eigh'

In [ ]:
#map to word and value pair and sort by value

word_to_pc1 = {k: X_pca[i, idx] for i, (k, v) in enumerate(data)}
word_to_pc1 = dict(sorted(word_to_pc1.items(), key=lambda item: item[1]))

for i, (k, v) in enumerate(word_to_pc1.items()):
	print(f"Word: {k:15s} => PC1: {v:.3f}")

Word: Leicestershire  => PC1: -0.326
Word: outdistances    => PC1: -0.325
Word: groundwater     => PC1: -0.322
Word: groundwater's   => PC1: -0.315
Word: Leicestershire's => PC1: -0.313
Word: outdistanced    => PC1: -0.311
Word: Rotherham       => PC1: -0.309
Word: undistinguishable => PC1: -0.308
Word: outdistance     => PC1: -0.302
Word: sunniest        => PC1: -0.301
Word: spiffiest       => PC1: -0.298
Word: solubles        => PC1: -0.298
Word: lepidolites     => PC1: -0.295
Word: Rhineland       => PC1: -0.292
Word: brierwoods      => PC1: -0.291
Word: indissolubility => PC1: -0.291
Word: Surrey          => PC1: -0.291
Word: surrey          => PC1: -0.291
Word: moats           => PC1: -0.290
Word: dissimilarities => PC1: -0.290
Word: Chelyabinsk     => PC1: -0.290
Word: diffraction's   => PC1: -0.289
Word: indistinguishably => PC1: -0.289
Word: spiculate       => PC1: -0.289
Word: combustibility's => PC1: -0.289
Word: indestructibility's => PC1: -0.287
Word: surreys         => PC1